In [1]:
import rasterio
import torch
import torch as nn
import numpy
import tqdm
import glob
import os
import pandas as pd

In [2]:
DEVICE = 'cuda' if torch.cuda.is_available() else 'cpu'
print('DEVICE using {}'.format(DEVICE))

DEVICE using cuda


In [3]:
from Model import cnn_model
from Model import cnn_model_attention

cnn1d = cnn_model.CNN1D
cnn1d_lstm = cnn_model.CNNLSTM
cnn2d = cnn_model.CNN2D
cnn2d_lstm = cnn_model.CNNLSTM2D
cnn1d_att = cnn_model_attention.CNN1DATT
cnn1dlstm_att = cnn_model_attention.CNNLSTMATT
cnn2d_att = cnn_model_attention.CNN2DATT
cnn2dlstm_att = cnn_model_attention.CNNLSTM2DATT

model_1D = {'model_cnn1d': cnn1d, 'model_cnn1d_lstm': cnn1d_lstm, 'model_cnn1d_att': cnn1d_att, 'model_cnn1dlstm_att': cnn1dlstm_att}
model_2D = {'model_cnn2d': cnn2d, 'model_cnn2d_lstm': cnn2d_lstm, 'model_cnn2d_att': cnn2d_att, 'model_cnn2dlstm_att': cnn2dlstm_att}

In [4]:
data = pd.read_csv("./treecrown_mergeAGB_6b_modelling.csv")
data.head()

AGB_edit  _b1_count    _b1_sum  _b1_mean_1  _b1_median  _b1_stdev  \
0  73.684983       5.00  43.800836    8.760167    9.365299   2.210602   
1  42.733037       1.99  20.624330   10.363985   10.034934   2.333843   
2  42.733037       0.18   2.177753   12.098628   12.242822   0.383257   
3  35.799332       0.31   3.706175   11.955403   11.863470   0.472929   
4  18.970996       6.00  71.179157   11.863193   11.765288   0.566136   

     _b1_min    _b1_max  _b1_range  _b1_minori  ...  _b62_mean  _b62_media  \
0   4.593345  11.108766   6.515420    4.593345  ...   0.081949   -0.064119   
1   5.627079  12.520593   6.893513    5.627079  ...  -0.027536   -0.023348   
2  11.657615  12.573362   0.915748   11.657615  ...  -0.059977    0.169837   
3  11.582809  12.679080   1.096271   11.582809  ...  -0.063205   -0.135772   
4  11.171371  12.979540   1.808168   11.171371  ...  -0.114903   -0.107663   

   _b62_stdev  _b62_min  _b62_max  _b62_range  _b62_minor  _b62_major  \
0    0.252381 -0.138926  0.549128    0.688054   -0.138926   -0.138926   
1    0.219720 -0.163573  0.411148    0.574720   -0.163573   -0.163573   
2    0.201298 -0.175354  0.175473    0.350827   -0.175354   -0.175354   
3    0.276983 -0.230118  0.380679    0.610797   -0.230118   -0.230118   
4    0.044661 -0.169886 -0.041692    0.128195   -0.169886   -0.169886   

   _b62_varie  _b62_varia  
0           5    0.063696  
1           8    0.048277  
2           3    0.040521  
3           3    0.076720  
4           6    0.001995  

[5 rows x 745 columns]

In [5]:
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

# Remove rows with NaN values
data = data.dropna()
data = data.fillna(0)  # or use another value suitable for your dataset

X = data.drop(columns=['AGB_edit']).values
y = data['AGB_edit'].values

y -= y.min()

# Step 3: Ensure there are no NaNs left (Optional but recommended for debugging)
assert not np.isnan(X).any(), "Features contain NaN values!"
assert not np.isnan(y).any(), "Target contains NaN values!"

#scaler = StandardScaler()
#X_scaled = scaler.fit_transform(X)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

# for 1D CNN
from torch.utils.data import DataLoader, TensorDataset

X_train_tensor = torch.tensor(X_train, dtype=torch.float32)
y_train_tensor = torch.tensor(y_train, dtype=torch.long)
X_test_tensor = torch.tensor(X_test, dtype=torch.float32)
y_test_tensor = torch.tensor(y_test, dtype=torch.long)

train_dataset = TensorDataset(X_train_tensor, y_train_tensor)
test_dataset = TensorDataset(X_test_tensor, y_test_tensor)

train_loader = DataLoader(train_dataset, batch_size=9, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=9, shuffle=False)

X_train.shape, X_test.shape, y_train.shape, y_test.shape

((86, 744), (38, 744), (86,), (38,))

In [6]:
#for 2D CNN
#X_reshaped = X_scaled.reshape(-1, 1, 6, 6)
X_reshaped = X.reshape(-1, 1, 12, 62) 
X_train2, X_test2, y_train2, y_test2 = train_test_split(X_reshaped, y, test_size=0.3, random_state=42)

X_train_tensor2 = torch.tensor(X_train2, dtype=torch.float32)
y_train_tensor2 = torch.tensor(y_train2, dtype=torch.long)
X_test_tensor2 = torch.tensor(X_test2, dtype=torch.float32)
y_test_tensor2 = torch.tensor(y_test2, dtype=torch.long)

train_dataset2 = TensorDataset(X_train_tensor2, y_train_tensor2)
test_dataset2 = TensorDataset(X_test_tensor2, y_test_tensor2)

train_loader2 = DataLoader(train_dataset2, batch_size=9, shuffle=True)
test_loader2 = DataLoader(test_dataset2, batch_size=9, shuffle=False)

X_train2.shape, X_test2.shape, y_train2.shape, y_test2.shape

((86, 1, 12, 62), (38, 1, 12, 62), (86,), (38,))

In [7]:
# Define training parameters
num_epochs = 10000
learning_rate = 0.001
input_size = X_train_tensor.shape[1] 
num_classes = 1

# Loss function
criterion = torch.nn.SmoothL1Loss()

print(input_size)
print(num_classes)

744
1


In [8]:
from torch.optim import SGD, Adam
from sklearn.metrics import r2_score

# Loop through each model in the model_list
for model_name, model_class in model_1D.items():
    print(f"Training {model_name}")

    # Initialize the model and move it to the device
    model = model_class(input_size=input_size).to(DEVICE)
    optimizer = SGD(model.parameters(), lr=learning_rate)

    # Metrics storage
    metrics = {
        "epoch": [],
        "train_loss": [],
        "train_r2": [],
        "test_loss": [],
        "test_r2": []
    }

    # Training loop
    for epoch in range(num_epochs):
        model.train()  # Set model to training mode
        running_loss = 0.0
        y_train_true = []
        y_train_pred = []

        for inputs, labels in train_loader:
            inputs, labels = inputs.float(), labels.float()
            inputs, labels = inputs.to(DEVICE), labels.to(DEVICE)

            optimizer.zero_grad()
            outputs = model(inputs).squeeze()
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()

            running_loss += loss.item()
            
            # Collect predictions for R² calculation
            y_train_true.extend(labels.cpu().numpy())
            y_train_pred.extend(outputs.detach().cpu().numpy())

        avg_train_loss = running_loss / len(train_loader)
        
        # Calculate R² score for training
        train_r2 = r2_score(y_train_true, y_train_pred)

        # Model Evaluation (on the test set)
        model.eval()
        running_val_loss = 0.0
        y_val_true = []
        y_val_pred = []
        with torch.no_grad():
            for inputs, labels in test_loader:  # Assume test_loader is already defined
                inputs, labels = inputs.float(), labels.float()
                inputs, labels = inputs.to(DEVICE), labels.to(DEVICE)
                outputs = model(inputs).squeeze()
                loss = criterion(outputs, labels)
                running_val_loss += loss.item()

                # Collect predictions for R² calculation
                y_val_true.extend(labels.cpu().numpy())
                y_val_pred.extend(outputs.cpu().numpy())

        avg_val_loss = running_val_loss / len(test_loader)
        
        # Calculate R² score for testing
        val_r2 = r2_score(y_val_true, y_val_pred)

        # Print metrics for each epoch
        print(f"Epoch [{epoch+1}/{num_epochs}], Train Loss: {avg_train_loss:.4f}, Train R2: {train_r2:.4f}, Test Loss: {avg_val_loss:.4f}, Test R2: {val_r2:.4f}")

        # Save metrics to dictionary
        metrics["epoch"].append(epoch + 1)
        metrics["train_loss"].append(avg_train_loss)
        metrics["train_r2"].append(train_r2)
        metrics["test_loss"].append(avg_val_loss)
        metrics["test_r2"].append(val_r2)

    # Save the model (optional)
    torch.save(model.state_dict(), f"{model_name}_best.pth")
    print(f"{model_name} saved as {model_name}_best.pth\n")

    # Save the metrics to a CSV file
    df = pd.DataFrame(metrics)
    df.to_csv(f"{model_name}_metrics.csv", index=False)
    print(f"Metrics for {model_name} saved as {model_name}_metrics.csv\n")

Training model_cnn1d
Epoch [1/10000], Train Loss: 71.8955, Train R2: -2.3922, Test Loss: 82.2609, Test R2: -2.4425
Epoch [2/10000], Train Loss: 67.5298, Train R2: -2.1534, Test Loss: 82.5182, Test R2: -2.4605
Epoch [3/10000], Train Loss: 63.0396, Train R2: -2.0570, Test Loss: 84.1467, Test R2: -2.8211
Epoch [4/10000], Train Loss: 66.7347, Train R2: -2.2050, Test Loss: 82.5750, Test R2: -2.4798
Epoch [5/10000], Train Loss: 65.5391, Train R2: -2.0922, Test Loss: 82.7665, Test R2: -2.5408
Epoch [6/10000], Train Loss: 64.1857, Train R2: -1.9499, Test Loss: 82.1641, Test R2: -2.4389
Epoch [7/10000], Train Loss: 68.4606, Train R2: -2.2503, Test Loss: 82.1483, Test R2: -2.4468
Epoch [8/10000], Train Loss: 66.0777, Train R2: -1.9238, Test Loss: 81.7722, Test R2: -2.4078
Epoch [9/10000], Train Loss: 66.6978, Train R2: -2.2496, Test Loss: 82.3365, Test R2: -2.5694
Epoch [10/10000], Train Loss: 64.1659, Train R2: -2.0682, Test Loss: 81.8574, Test R2: -2.4687
Epoch [11/10000], Train Loss: 66.8791,

In [9]:
from torch.optim import SGD
from sklearn.metrics import r2_score
input_size = (1, 12, 62)
num_classes = 1

# Loop through each model in the model_list
for model_name, model_class in model_2D.items():
    print(f"Training {model_name}")

    # Initialize the model and move it to the device
    model = model_class(input_size=input_size, num_classes=num_classes).to(DEVICE)
    optimizer = SGD(model.parameters(), lr=learning_rate)

    # Metrics storage
    metrics = {
        "epoch": [],
        "train_loss": [],
        "train_r2": [],
        "test_loss": [],
        "test_r2": []
    }

    # Training loop
    # Training loop
    for epoch in range(num_epochs):
        model.train()  # Set model to training mode
        running_loss = 0.0
        y_train_true = []
        y_train_pred = []

        for inputs, labels in train_loader2:
            inputs, labels = inputs.float(), labels.float()
            inputs, labels = inputs.to(DEVICE), labels.to(DEVICE)

            optimizer.zero_grad()
            outputs = model(inputs).squeeze()
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()

            running_loss += loss.item()
            
            # Collect predictions for R² calculation
            y_train_true.extend(labels.cpu().numpy())
            y_train_pred.extend(outputs.detach().cpu().numpy())

        avg_train_loss = running_loss / len(train_loader)
        
        # Calculate R² score for training
        train_r2 = r2_score(y_train_true, y_train_pred)

        # Model Evaluation (on the test set)
        model.eval()
        running_val_loss = 0.0
        y_val_true = []
        y_val_pred = []
        with torch.no_grad():
            for inputs, labels in test_loader2:  # Assume test_loader is already defined
                inputs, labels = inputs.float(), labels.float()
                inputs, labels = inputs.to(DEVICE), labels.to(DEVICE)
                outputs = model(inputs).squeeze()
                loss = criterion(outputs, labels)
                running_val_loss += loss.item()

                # Collect predictions for R² calculation
                y_val_true.extend(labels.cpu().numpy())
                y_val_pred.extend(outputs.cpu().numpy())

        avg_val_loss = running_val_loss / len(test_loader)
        
        # Calculate R² score for testing
        val_r2 = r2_score(y_val_true, y_val_pred)

        # Print metrics for each epoch
        print(f"Epoch [{epoch+1}/{num_epochs}], Train Loss: {avg_train_loss:.4f}, Train R2: {train_r2:.4f}, Test Loss: {avg_val_loss:.4f}, Test R2: {val_r2:.4f}")

        # Save metrics to dictionary
        metrics["epoch"].append(epoch + 1)
        metrics["train_loss"].append(avg_train_loss)
        metrics["train_r2"].append(train_r2)
        metrics["test_loss"].append(avg_val_loss)
        metrics["test_r2"].append(val_r2)

    # Save the model (optional)
    torch.save(model.state_dict(), f"{model_name}_best.pth")
    print(f"{model_name} saved as {model_name}_best.pth\n")

    # Save the metrics to a CSV file
    df = pd.DataFrame(metrics)
    df.to_csv(f"{model_name}_metrics.csv", index=False)
    print(f"Metrics for {model_name} saved as {model_name}_metrics.csv\n")

Training model_cnn2d
Epoch [1/10000], Train Loss: 46.4894, Train R2: -0.7260, Test Loss: 46.6125, Test R2: -0.0019
Epoch [2/10000], Train Loss: 36.4634, Train R2: -0.0061, Test Loss: 46.4660, Test R2: -0.2348
Epoch [3/10000], Train Loss: 39.9405, Train R2: -0.1627, Test Loss: 52.3240, Test R2: -0.2202
Epoch [4/10000], Train Loss: 42.7170, Train R2: -0.2689, Test Loss: 46.0237, Test R2: -0.0221
Epoch [5/10000], Train Loss: 38.2816, Train R2: -0.0494, Test Loss: 47.3176, Test R2: -0.0026
Epoch [6/10000], Train Loss: 40.1608, Train R2: -0.1298, Test Loss: 48.3770, Test R2: -0.0331
Epoch [7/10000], Train Loss: 41.7204, Train R2: -0.1876, Test Loss: 48.1132, Test R2: -0.0237
Epoch [8/10000], Train Loss: 40.0298, Train R2: -0.0612, Test Loss: 46.4127, Test R2: -0.2301
Epoch [9/10000], Train Loss: 39.6853, Train R2: -0.1697, Test Loss: 47.1660, Test R2: -0.0001
Epoch [10/10000], Train Loss: 38.9644, Train R2: -0.0105, Test Loss: 45.6553, Test R2: -0.1629
Epoch [11/10000], Train Loss: 40.1005,